<a href="https://colab.research.google.com/github/rdaniello/DataVizFall2020_Colab/blob/master/States_Class_Activity_Week03.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd
import folium
import json

In [2]:
### (1) read covid data from NYT
db = "https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-counties.csv"
df = pd.read_csv(db)

In [3]:
# 2 (A) filter by date
# 2 (B) group by state name, and sum the cases numbers of all the counties of each state
def covid_stat_on(df,strDate):
    df_temp = df[df['date']==strDate][['state','cases','deaths','date']].groupby('state',as_index = False)\
                                                                .sum().copy()\
                                                                .dropna()\
                                                                .reset_index(drop=True)
    return df_temp

In [4]:
# 3 (A) Load GeoJSON
state_geo_json = "https://raw.githubusercontent.com/rdaniello/DataVizFall2020_Colab/master/cb_2018_us_state_5m.json"
df_state_geo_json = pd.read_json(state_geo_json)

#df_state_geo_json['features'].iloc[0]

In [5]:
# 3 (B) Make a dictionary of State names and 2 Letter ID using the GeoJSON database
state_abbrv={}
for i in range(len(df_state_geo_json['features'])):
    state_abbrv[df_state_geo_json['features'].iloc[i]['properties']['NAME']] = df_state_geo_json['features'].iloc[i]['properties']['STUSPS']
state_abbrv

{'Alabama': 'AL',
 'Alaska': 'AK',
 'American Samoa': 'AS',
 'Arizona': 'AZ',
 'Arkansas': 'AR',
 'California': 'CA',
 'Colorado': 'CO',
 'Commonwealth of the Northern Mariana Islands': 'MP',
 'Connecticut': 'CT',
 'Delaware': 'DE',
 'District of Columbia': 'DC',
 'Florida': 'FL',
 'Georgia': 'GA',
 'Guam': 'GU',
 'Hawaii': 'HI',
 'Idaho': 'ID',
 'Illinois': 'IL',
 'Indiana': 'IN',
 'Iowa': 'IA',
 'Kansas': 'KS',
 'Kentucky': 'KY',
 'Louisiana': 'LA',
 'Maine': 'ME',
 'Maryland': 'MD',
 'Massachusetts': 'MA',
 'Michigan': 'MI',
 'Minnesota': 'MN',
 'Mississippi': 'MS',
 'Missouri': 'MO',
 'Montana': 'MT',
 'Nebraska': 'NE',
 'Nevada': 'NV',
 'New Hampshire': 'NH',
 'New Jersey': 'NJ',
 'New Mexico': 'NM',
 'New York': 'NY',
 'North Carolina': 'NC',
 'North Dakota': 'ND',
 'Ohio': 'OH',
 'Oklahoma': 'OK',
 'Oregon': 'OR',
 'Pennsylvania': 'PA',
 'Puerto Rico': 'PR',
 'Rhode Island': 'RI',
 'South Carolina': 'SC',
 'South Dakota': 'SD',
 'Tennessee': 'TN',
 'Texas': 'TX',
 'United States

In [6]:
# 4 Get sample data for 1 day (09/13/2020)
covid_stat = covid_stat_on(df,'2020-09-13')
covid_stat.head(1)

state   cases  deaths
0  Alabama  138755    2351

In [7]:
state_abbrv.keys()

dict_keys(['Nebraska', 'Washington', 'New Mexico', 'South Dakota', 'Texas', 'California', 'Kentucky', 'Ohio', 'Alabama', 'Georgia', 'Wisconsin', 'Oregon', 'Pennsylvania', 'Mississippi', 'Missouri', 'North Carolina', 'Oklahoma', 'West Virginia', 'New York', 'Indiana', 'Kansas', 'Idaho', 'Nevada', 'Vermont', 'Montana', 'Minnesota', 'North Dakota', 'Hawaii', 'Arizona', 'Delaware', 'Rhode Island', 'Colorado', 'Utah', 'Virginia', 'Wyoming', 'Louisiana', 'Michigan', 'Massachusetts', 'Florida', 'United States Virgin Islands', 'Connecticut', 'New Jersey', 'Maryland', 'South Carolina', 'Maine', 'New Hampshire', 'District of Columbia', 'Guam', 'Commonwealth of the Northern Mariana Islands', 'American Samoa', 'Iowa', 'Puerto Rico', 'Arkansas', 'Tennessee', 'Illinois', 'Alaska'])

In [8]:
# Translate state name to state 2 letter code
covid_stat_translated = covid_stat[covid_stat['state'].isin(state_abbrv.keys())].copy()
covid_stat_translated['state'] = covid_stat_translated['state'].apply(lambda x:state_abbrv[x] )

In [9]:
covid_stat_translated.head()


state   cases  deaths
0    AL  138755    2351
1    AK    7136      41
2    AZ  208514    5322
3    AR   70219     981
4    CA  763389   14386

[Link to map](https://rdaniello.github.io/DataVizFall2020_Colab/)

In [10]:
# code to add tooltip cases and deaths to geojson
import requests
resp = requests.get(state_geo_json)  # get the raw file
data = json.loads(resp.text)             # get the jason

for feature in data['features']:     # for each feature
  # add value of case and deaths in feature property
  tmp_df = covid_stat_translated[covid_stat_translated['state'] == feature['properties']['STUSPS']]

  if(tmp_df.shape[0] > 0):
    feature['properties']['cases'] = int(tmp_df.iloc[0]['cases'])
    feature['properties']['deaths'] = int(tmp_df.iloc[0]['deaths'])

# dump edited geojsn back to original geojason
state_geo_json_tt = json.dumps(data)

fff = data['features'][0]

print(fff['properties'])


{'STATEFP': '31', 'STATENS': '01779792', 'AFFGEOID': '0400000US31', 'GEOID': '31', 'STUSPS': 'NE', 'NAME': 'Nebraska', 'LSAD': '00', 'ALAND': 198956658395, 'AWATER': 1371829134, 'cases': 38188, 'deaths': 449}


In [11]:
m = folium.Map(
            location=[48, -102], # center the map to this point
            zoom_start=4)        # starting zoom!

#Choropleth layer - data function returns log of cases
choro1 = folium.Choropleth(
    geo_data=state_geo_json_tt, ## load the downloaded GeoJSON (mapshaper.org converted)
    name='Covid-19 State Cases',          ## add a name for the layer
    legend_name='Actual State Covid-19 Cases',  ## add legend topic
    data=covid_stat_translated,   ## pass our covid-19 data to the layer method
    columns=['state','cases'],             ## the columns from our data
    key_on='feature.properties.STUSPS',    ## the state
    fill_color='YlOrRd',                    ## color style BuGn, BuPu, GnBu, OrRd, PuBu, PuBuGn, PuRd, RdPu, YlGn, YlGnBu, YlOrBr, and YlOrRd
    bins=9,                               ## number of bins usef of color codding 
    fill_opacity=0.7,
    line_opacity=0.2,
    nan_fill_color='blue',
    highlight=True,
    show=False
).add_to(m)

choro2 = folium.Choropleth(
    geo_data=state_geo_json_tt,
    name='Covid-19 State Deaths',
    legend_name='Actual State Covid-19 Deaths',
    data=covid_stat_translated,
    columns=['state','deaths'],
    key_on='feature.properties.STUSPS',
    fill_color='YlGnBu',
    bins=9,
    fill_opacity=0.7,
    line_opacity=0.2,
    nan_fill_color='none',
    highlight=True,
     show=True).add_to(m)

#tooltips
choro1.geojson.add_child(
    folium.features.GeoJsonTooltip(
        fields=['NAME', 'cases'], 
        aliases=['State', 'Cases'],
        labels=True)
)

choro2.geojson.add_child(
    folium.features.GeoJsonTooltip(
        fields=['NAME', 'deaths'], 
        aliases=['State', 'Deaths'],
        labels=True)
)

folium.LayerControl().add_to(m)

m




In [12]:
m.save('index.html')